In [ ]:
from SPARQLWrapper import SPARQLWrapper, JSON
import pandas as pd

In [ ]:

sparql = SPARQLWrapper("https://query.wikidata.org/sparql")

# Define the SPARQL query to fetch data about cities and municipalities in Spain
query = """
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX wikibase: <http://wikiba.se/ontology#>
PREFIX wd: <http://www.wikidata.org/entity/>
PREFIX wdt: <http://www.wikidata.org/prop/direct/>
SELECT ?instance ?instanceLabel ?class ?classLabel ?country ?countryLabel WHERE {
  ?instance wdt:P31 wd:Q16917.   # Instance of building (Q16917) or its subclasses
  ?instance wdt:P31 ?class .               # Get the class of the instance
  
  ?instance wdt:P17 ?country .             # The instance is located in a country
  
   VALUES ?country { 
    wd:Q29 wd:Q45 wd:Q142 wd:Q233 wd:Q41 wd:Q38 wd:Q183 wd:Q31 wd:Q55 
    wd:Q34 wd:Q20 wd:Q33 wd:Q211 wd:Q191 wd:Q37 wd:Q36 wd:Q28 wd:Q218 
    wd:Q214 wd:Q213 wd:Q215
  }
  SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }  # Get labels in English
}
"""

# Set the query and request JSON results
sparql.setQuery(query)
sparql.setReturnFormat(JSON)

# Execute the query and fetch results
results = sparql.query().convert()

# Process the results into a list of dictionaries
wikidata_data = []
for result in results["results"]["bindings"]:
    hospital = {
        "name": result["instanceLabel"]["value"],
        "class": result["classLabel"]["value"] if "classLabel" in result else None,
        "country": result["countryLabel"]["value"] if "countryLabel" in result else None
    }
    wikidata_data.append(hospital)

# Convert the list of dictionaries to a pandas DataFrame
df_wikidata = pd.DataFrame(wikidata_data)
display(df_wikidata)

In [20]:
import requests
import folium
import pandas as pd
from IPython.display import display

# List of countries to query
countries = ['ES', 'PT', 'FR', 'MT', 'GR', 'IT', 'DE', 'BE', 'NL', 'SE', 
             'NO', 'FI', 'LV', 'EE', 'LT', 'PL', 'HU', 'RO', 'SK', 'CZ', 'SI']

def query_hospitals_in_country(country):
    # Overpass API query to find hospitals in the specified country
    overpass_url = "http://overpass-api.de/api/interpreter"
    
    overpass_query = f"""
    [out:json];
    area["ISO3166-1"="{country}"];
    (
      node["amenity"="hospital"](area);
      way["amenity"="hospital"](area);
      relation["amenity"="hospital"](area);
    );
    out center;
    """
    
    # Sending the request to the Overpass API
    response = requests.post(overpass_url, data={'data': overpass_query})
    
    if response.status_code == 200:
        # Load the response as JSON
        hospitals_data = response.json()
        
        # Create a list to store hospital information
        hospitals = []
        for element in hospitals_data['elements']:
            hospital_name = element.get('tags', {}).get('name', 'Unnamed Hospital')
            
            if 'lat' in element and 'lon' in element:
                hospitals.append({
                    'name': hospital_name,
                    'latitude': element['lat'],
                    'longitude': element['lon'],
                    'country': country
                })
        return pd.DataFrame(hospitals)
    else:
        print(f"Error for country {country}: {response.status_code}")
        return pd.DataFrame()  # Return an empty DataFrame on error

def query_hospitals_in_countries():
    # Initialize an empty DataFrame to append results
    all_hospitals_df = pd.DataFrame()

    # Query hospitals for each country and append to the DataFrame
    for country in countries:
        country_hospitals_df = query_hospitals_in_country(country)
        all_hospitals_df = pd.concat([all_hospitals_df, country_hospitals_df], ignore_index=True)

    return all_hospitals_df

# Main execution
df_openstreetmap = query_hospitals_in_countries()

KeyboardInterrupt: 

In [19]:

from folium.plugins import MarkerCluster
def plot_hospitals_on_map(hospitals_df):
    # Create a map centered around Europe
    m = folium.Map(location=[50, 10], zoom_start=4)  # Centered around Central Europe

    # Create a MarkerCluster
    marker_cluster = MarkerCluster().add_to(m)

    # Add hospital markers to the map
    for _, hospital in hospitals_df.iterrows():
        folium.Marker(
            location=[hospital['latitude'], hospital['longitude']],
            popup=f"{hospital['name']} ({hospital['country']})",
            icon=folium.Icon(color='blue')
        ).add_to(marker_cluster)

    # Display the map in the notebook
    display(m)

if not df_openstreetmap.empty:
    plot_hospitals_on_map(df_openstreetmap)
else:
    print("No hospitals found.")

                                name   latitude  longitude country
0       Hospital Universitario La Fe  39.483788  -0.390449      ES
1           Hospital de La Magdalena  40.004387  -0.072897      ES
2              Centro de Salud Arona  28.097977 -16.682177      ES
3                Consultorio Arguayo  28.269544 -16.807097      ES
4                   Unnamed Hospital  28.164896 -17.197944      ES
...                              ...        ...        ...     ...
2838                   Ambulanta Kus  46.044074  14.508366      SI
2839                Unnamed Hospital  46.153465  15.046992      SI
2840         Zdravstveni dom Brežice  45.908034  15.594031      SI
2841        Zdravstveni dom Cerknica  45.791274  14.365674      SI
2842  Služba nujne medicinske pomoči  46.425552  15.875041      SI

[2843 rows x 4 columns]


In [ ]:
print(len(df_openstreetmap))

In [44]:
import json
import ast

df_opensearch = pd.read_csv('ca_extraction.csv')
ca_list = sum(df_opensearch['Contracting Authorities'].apply(ast.literal_eval))

TypeError: unsupported operand type(s) for +: 'int' and 'list'

In [43]:
display(ca_list)

0         [{'Name': 'МБАЛ Света Петка АД', 'National ID'...
1         [{'Name': 'INSTITUTUL DE PSIHIATRIE "SOCOLA" I...
2         [{'Name': 'HOSPITAL CLINICO SAN CARLOS DE MADR...
3         [{'Name': 'Spital Clinic Judetean de Urgenta A...
4         [{'Name': 'SPITAL CLINIC JUDETEAN DE URGENTA O...
                                ...                        
182868    [{'Name': 'ZZOZ w Ostrowie Wielkopolskim', 'Na...
182869    [{'Name': 'Staatliche Feuerwehrschule Regensbu...
182870    [{'Name': 'Samodzielny Publiczny Szpital Klini...
182871    [{'Name': 'Nemocnice České Budějovice, a.s.', ...
182872    [{'Name': 'Technische Universität Ilmenau, Dez...
Name: Contracting Authorities, Length: 182873, dtype: object